<a href="https://colab.research.google.com/github/MilSur/CuMnAs/blob/main/reports/Correlation%20Experiment/Delay%20scan%20with%20classic%20switching.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [8]:
!git clone https://github.com/MilSur/CuMnAs.git
!pip install kmeans1d
!pip install plotly --upgrade

from CuMnAs.scripts.opticalWriting import DataProcessing
import numpy as np
import os
import plotly.graph_objects as go
import warnings
warnings.filterwarnings("ignore")

fatal: destination path 'CuMnAs' already exists and is not an empty directory.
Requirement already up-to-date: plotly in /usr/local/lib/python3.7/dist-packages (5.0.0)


In [9]:
#@title Relaxace v reálném čase
from plotly.subplots import make_subplots

directory = "/content/CuMnAs/data/P074n35/experiment/"

curves_names = [os.path.splitext(filename)[0] for filename in os.listdir(directory) if os.path.splitext(filename)[1] == '.dat']
file_translate = {float(curve.replace('_', '.')):curve for curve in curves_names}
curves = [float(curve.replace('_', '.')) for curve in curves_names]
curves.sort()

fig = make_subplots(rows=2, cols=1, shared_xaxes=True, vertical_spacing=0.01)

for curve in curves:
    data = DataProcessing(directory+file_translate[curve])
    X = data.R4[:, 0]
    R4 = data.R4[:, 1]
    data.pulses[0,0]
    fig.append_trace(go.Scatter(
        visible=False,
        x= (data.R4[:, 0]-data.pulses[0,0]),
        y=data.R4[:, 1],
    ), row=1, col=1)
    
    fig.append_trace(go.Bar(
        visible=False,
        x= (data.pulses[:,0]-data.pulses[0,0]),
        y=data.pulses[:,1],
        width = 0.3,
    ), row=2, col=1)


fig.data[0].visible = True    
fig.data[1].visible = True


steps = []
for i in range(len(curves)):
    step = dict(
        method="update",
        args=[{"visible": [False] * len(fig.data)},
              {"title": "Time Delay: " + str(round(6.6*curves[i]/1000, 3))+" ns"}],
        label=str(round(6.6*curves[i]/1000, 3)),
        # layout attribute
    )
    step["args"][0]["visible"][2*i] = True  # Toggle i'th trace to "visible"
    step["args"][0]["visible"][2*i+1] = True
    steps.append(step)

sliders = [dict(
    active=0,
    currentvalue={"prefix": "Time Delay (ns): "},
    pad={"t": 50},
    steps=steps
)]

fig.update_layout(
    sliders=sliders
)

fig.update_yaxes(title_text="Resistivity (ohms)", row=1, col=1, range=[43,43.3])
fig.update_yaxes(title_text="Intensity (mW)", row=2, col=1)
fig.update_xaxes(title_text="Time (s)", row=2, col=1)


fig.update_layout(showlegend=False)
fig.show()

In [10]:
#@title Korelační křivky
from scipy.optimize import curve_fit

directory = "/content/CuMnAs/data/P074n35/experiment/"

curves_names = [os.path.splitext(filename)[0] for filename in os.listdir(directory) if os.path.splitext(filename)[1] == '.dat']
curves_names.sort()

dep = []
for curve in curves_names:
    params = np.mean(DataProcessing(directory+curve).processWOFitting(1, 5, 5, 9), axis = 0)
    position = float(curve.replace('_', '.'))
    dep.append(np.append([position], params))
dep = np.array(dep)
xdata=-6.6*dep[:,0]/1000+2.31
ydata_switching=1000*dep[:,1] 
ydata_spikes=1000*dep[:,2]

fig = go.Figure()

#fig.add_trace(go.Scatter(x=-6.6*dep[:,0]/1000+2.31, y=dep[:,1]*1000, mode='markers', name=curve))
#fig.add_trace(go.Scatter(x=-6.6*dep[:,0]/1000+2.31, y=1000*dep[:,1], error_y=dict(type='data', array=1000*dep[:,3], visible=True, thickness=0.1), mode='markers', name='Amplitude'))
#fig.add_trace(go.Scatter(x=-6.6*dep[:,0]/1000+2.31, y=1000*dep[:,2], error_y=dict(type='data', array=1000*dep[:,3], visible=True, thickness=0.1), mode='markers', name='P&p: (37, 15) mW'))

fig.add_trace(go.Scatter(x=xdata, y=ydata_switching, legendgroup = 'Switching', error_y=dict(type='data', array=1000*dep[:,3], visible=True, thickness=0.1), mode='markers', name='Switching'))
fig.add_trace(go.Scatter(x=xdata, y=ydata_spikes, legendgroup = 'Spikes', mode='markers', name='Spikes'))

def decay(x, A, tau, C):
    return A * np.exp(-x/tau) + C

filtr = xdata>0
# 1.295 ns - Switching
popt1, pcov1 = curve_fit(decay, xdata[filtr], ydata_switching[filtr], bounds=([0, 1.295, 0], [200, 2, 5]))
fig.add_trace(go.Scatter(x=xdata[filtr], y=decay(xdata[filtr], *popt1), legendgroup = 'Switching', mode='markers', name='τ = 1.295 ns'))
# 1.295 ns - Spikes
popt2, pcov2 = curve_fit(decay, xdata[filtr], ydata_spikes[filtr], bounds=([0, 1.295, 0], [200, 2, 5]))
fig.add_trace(go.Scatter(x=xdata[filtr], y=decay(xdata[filtr], *popt2), legendgroup = 'Spikes', mode='markers', name='τ = 1.295 ns'))

# Free fit - Switching
popt3, pcov3 = curve_fit(decay, xdata[filtr], ydata_switching[filtr], bounds=([0, 0, 0], [200, 2, 5]))
fig.add_trace(go.Scatter(x=xdata[filtr], y=decay(xdata[filtr], *popt3), legendgroup = 'Switching', mode='markers', name='τ = 0.55 ns'))













xdata=-6.6*dep[:,0]/1000+2.31
ydata=1000*dep[:,1]
xdata = np.array(xdata)
ydata = np.array(ydata)

filtr = xdata>0
xdata = xdata[filtr]
ydata = ydata[filtr]
#popt, pcov = curve_fit(decay, xdata, ydata, bounds=([0, 1.295, 0], [200, 2, 5]))

#fig.add_trace(go.Scatter(x=xdata, y=decay(xdata, *popt), mode='markers', name='fit'))
#print(popt)


#fig.add_trace(go.Scatter(x=dep[:,0], y=dep[:,2], error_y=dict(type='data', array=dep[:,3], visible=True, thickness=0.1), mode='markers', name=curve))
#fig.add_trace(go.Scatter(x=dep[:,0], y=dep[:,3], mode='markers', name=curve))

path = "../data/"
files = ['Bb1', 'Bb2', 'Bb3', 'Bb4','Bb5', 'Bb6']
files = []

for j, curve in enumerate(files):
    data = np.loadtxt(path+curve+".dat", skiprows=1)
    starts = np.argwhere(data[:,0] == np.amin(data[:,0]))
    starts = [i[0] for i in starts]
    cycles = np.split(data, starts, axis=0)
    averaged = np.mean(cycles[1:], axis=0)
    
    fig.add_trace(go.Scatter(x=averaged[:,0]/1000000, y=6000*averaged[:,3],
                        mode='markers+lines',
                    name='P&p: ({}, 7) mW'.format(20+j*4)))



fig.update_xaxes(zeroline=True, zerolinewidth=2, zerolinecolor='LightPink', title_text="Time Delay (ns)")
fig.update_yaxes(zeroline=True, zerolinewidth=2, zerolinecolor='LightPink', title_text="Amplitude (mOhms)")


fig.show()

JAP:
50 nm -> tau = 1.295 ns 